<h1><center>Data Wrangling - Meta File</center></h1>

Import the libraries

In [1]:
import pandas as pd
import numpy as np
import gc

Read the meta file into a dataframe. 

In [2]:
beauty = pd.read_csv('meta_beauty.csv',index_col=0)
beauty.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 259204 entries, 0 to 259203
Data columns (total 9 columns):
asin           259204 non-null object
description    232202 non-null object
title          258760 non-null object
imUrl          259116 non-null object
salesRank      254016 non-null object
categories     259204 non-null object
price          189930 non-null float64
related        207854 non-null object
brand          127039 non-null object
dtypes: float64(1), object(8)
memory usage: 19.8+ MB


In [3]:
beauty.head(2)

asin                                        description  \
0  0205616461  As we age, our once youthful, healthy skin suc...   
1  0558925278  Mineral Powder Brush--Apply powder or mineral ...   

                                               title  \
0  Bio-Active Anti-Aging Serum (Firming Ultra-Hyd...   
1  Eco Friendly Ecotools Quality Natural Bamboo C...   

                                               imUrl  \
0  http://ecx.images-amazon.com/images/I/41DecrGO...   
1  http://ecx.images-amazon.com/images/I/51L%2BzY...   

                            salesRank  \
0  {'Health & Personal Care': 461765}   
1                  {'Beauty': 402875}   

                                          categories  price related brand  
0  [['Beauty', 'Skin Care', 'Face', 'Creams & Moi...    NaN     NaN   NaN  
1  [['Beauty', 'Tools & Accessories', 'Makeup Bru...    NaN     NaN   NaN

The dataset contains 259204 observations and 10 columns.  

Let's first check for the unique values in ProductID column. We want to make sure the ID data is not duplicated.

In [4]:
beauty.asin.value_counts(ascending=False).head()

B0009OAGQA    1
B0089NNH1Y    1
B000C1ZEYY    1
B004Y9GTOO    1
B00DURDULQ    1
Name: asin, dtype: int64

Each product ID has only 1 record, so it is safe to say that there are no duplicates.

Check for missing values in all the columns

In [5]:
beauty.isnull().sum()

asin                0
description     27002
title             444
imUrl              88
salesRank        5188
categories          0
price           69274
related         51350
brand          132165
dtype: int64

In [6]:
beauty['brand'].unique()

array([nan, 'Max Factor', 'M.A.C', ..., 'Rebirth INC', 'Natural Beauty',
       'Miracurl'], dtype=object)

51% of the items are missing brand information. We can merge this column with the title and then drop the 2 individual columns.

In [7]:
beauty['brand_title'] = beauty['brand'].fillna('') + ' ' + beauty['title'].fillna('')

In [8]:
beauty.isnull().sum()

asin                0
description     27002
title             444
imUrl              88
salesRank        5188
categories          0
price           69274
related         51350
brand          132165
brand_title         0
dtype: int64

26% items are missing price information. We may still be able to use it for analysis.  
All columns except categories have missing values in them. We will have to determine whether to drop the rows with missing values or correct them or impute them. The image url column will not be used in this project and can be dropped.

In [9]:
columns = ['imUrl', 'title', 'brand']
beauty.drop(columns, inplace=True, axis=1)

The salesRank column is in dictionary form (key-value pair). To clean it, we should convert the key to a column and the value to column value.

In [10]:
beauty['salesRank'] = beauty['salesRank'].fillna("{'Beauty': 0}")
import ast
beauty['salesRank'] = beauty['salesRank'].apply(lambda x: ast.literal_eval(x))
splitcol = beauty['salesRank'].apply(pd.Series)
data = pd.concat([beauty, splitcol], axis=1).drop('salesRank', axis=1)

Since we will be dealing only with Beauty and Personal items category and the product ranking in other categories is not relevant, all other newly created columns should be dropped.

In [11]:
columns = ['Music', 'Home &amp; Kitchen', 'Movies & TV', 'Patio, Lawn & Garden', 'Pet Supplies', 'Kitchen & Dining', 'Sports &amp; Outdoors', 'Magazines', 'Clothing', 'Electronics', 'Toys & Games',  'Arts, Crafts & Sewing', 'Grocery & Gourmet Food', 'Industrial & Scientific', 'Camera &amp; Photo', 'Office Products', 'Musical Instruments', 'Jewelry', 'Automotive', 'Shoes',  'Watches', 'Baby', 'Home Improvement', 'Software', 'Cell Phones & Accessories', 'Books', 'Computers & Accessories']
data.drop(columns, inplace=True, axis=1)

In [12]:
data.head(20)

asin                                        description  \
0   0205616461  As we age, our once youthful, healthy skin suc...   
1   0558925278  Mineral Powder Brush--Apply powder or mineral ...   
2   0733001998  From the Greek island of Chios, this Mastiha b...   
3   0737104473  Limited edition Hello Kitty Lipstick featuring...   
4   0762451459  The mermaid is an elusive (okay, mythical) cre...   
5   1304139212  A pencil designed for shaping, lining or filli...   
6   130414674X  What it is:A magical makeup sealer. What it do...   
7   130414089X  Length : 13.5 cm\nColor: Black\n100% Brand new...   
8   1304196062  Lasting Performance Liquid Make-up feels natur...   
9   1304146537  Eyliplex-2 is a dual solution that focuses on ...   
10  130414643X  Eyliplex-2 is a dual solution that focuses on ...   
11  1304174905  INSTANTLY REVITALIZE SKIN MOIST THE FACE OF HI...   
12  1304196135  Max Factor Face Care  Max Factor Lasting Perfo...   
13  1304139220  A pencil designed for shaping, lining or filli...   
14  1304168522  A brightening BB Cream that re-illuminates ski...   
15  1304174867  Pure natural honey extract contains a variety ...   
16  1304196070  Lasting Performance Liquid Make-up feels natur...   
17  1304196046  Lasting Performance Liquid Make-up feels natur...   
18  1304351475  Too Faced *Natural Eyes Shadow Palette* \n\nCo...   
19  1304174778  Strawberry berry tea -- anti-wrinkle nourishin...   

                                           categories  price  \
0   [['Beauty', 'Skin Care', 'Face', 'Creams & Moi...    NaN   
1   [['Beauty', 'Tools & Accessories', 'Makeup Bru...    NaN   
2   [['Beauty', 'Skin Care', 'Body', 'Moisturizers...    NaN   
3          [['Beauty', 'Makeup', 'Lips', 'Lipstick']]    NaN   
4   [['Beauty', 'Tools & Accessories', 'Mirrors', ...  19.98   
5        [['Beauty', 'Makeup', 'Lips', 'Lip Liners']]    NaN   
6               [['Beauty', 'Makeup', 'Makeup Sets']]    NaN   
7          [['Beauty', 'Makeup', 'Eyes', 'Eyeliner']]    NaN   
8        [['Beauty', 'Makeup', 'Face', 'Foundation']]    NaN   
9   [['Beauty', 'Skin Care', 'Eyes', 'Dark Circle ...    NaN   
10  [['Beauty', 'Skin Care', 'Eyes', 'Dark Circle ...    NaN   
11  [['Beauty', 'Skin Care', 'Face', 'Creams & Moi...   9.99   
12       [['Beauty', 'Makeup', 'Face', 'Foundation']]  27.59   
13       [['Beauty', 'Makeup', 'Lips', 'Lip Liners']]  24.13   
14  [['Beauty', 'Skin Care', 'Sun', 'Skin Protecti...    NaN   
15  [['Beauty', 'Skin Care', 'Face', 'Creams & Moi...    NaN   
16       [['Beauty', 'Makeup', 'Face', 'Foundation']]    NaN   
17       [['Beauty', 'Makeup', 'Face', 'Foundation']]    NaN   
18       [['Beauty', 'Makeup', 'Eyes', 'Eye Shadow']]  33.99   
19  [['Beauty', 'Skin Care', 'Face', 'Creams & Moi...    NaN   

                                              related  \
0                                                 NaN   
1                                                 NaN   
2                                                 NaN   
3                                                 NaN   
4                                                 NaN   
5                                                 NaN   
6                                                 NaN   
7   {'also_viewed': ['B00KX7A30W', 'B004L6DE3Y', '...   
8                                                 NaN   
9   {'also_bought': ['B002J2KOXK', 'B008TCVZ6Y'], ...   
10  {'also_bought': ['B002J2KOXK', 'B005CYJII4', '...   
11                    {'also_viewed': ['B007X8VP10']}   
12  {'also_bought': ['B001GNBVU8', 'B002MEWGDG', '...   
13  {'also_bought': ['B006RRY4NE'], 'bought_togeth...   
14                                                NaN   
15                                                NaN   
16                    {'also_bought': ['B00CHLSN3Q']}   
17                                                NaN   
18  {'also_bought': ['B00AVUE1S6', 'B00AYCOLMC', '...   
19  {'also_viewed': ['B00EHFSJSO', 'B00J4CGIYW', '...   

                 

Enable gc and perform garbage collection to free up memory.

In [13]:
gc.enable()
gc.collect()

1814502

Check for unique values in related and categories

In [13]:
data['related'].unique()

array([nan,
       "{'also_viewed': ['B00KX7A30W', 'B004L6DE3Y', 'B000FBF58G', 'B00HEPJGVS', 'B00LBQ49DG', 'B0034ZU56W', 'B00F29W6XS', 'B000FBF59A', 'B003HG4VLS', 'B008JVJ77Y', 'B00BPCG592', 'B000FBLTIQ', 'B006KTTGC8', 'B008Y03O7E', 'B006UET4XE', 'B009AK5EQG', 'B00F0KWBCU', 'B00J3UG1B0', 'B00HCC6J6S', 'B000FBNYRU', 'B00DQ3SWYE', 'B00C89Z5KG', 'B009O560CE', 'B000FBNYSY', 'B00KN0HYU6', 'B00HF6SJVY', 'B003ZS6OJK', 'B001L1H8DY', 'B00HLF8C3O', 'B008UXYQ8G', 'B00IJ3LG94', 'B003OIPJZ6', 'B009Q1YPVY', 'B00AMYNT8E', 'B00LBD64NW', 'B00EU6NK66', 'B001TK1I4M', 'B00KVBZAXK', 'B00ITCAR40', 'B004TSFE28', 'B008GOR6O0', 'B004TSFBNK', 'B00EYZR3E8']}",
       "{'also_bought': ['B002J2KOXK', 'B008TCVZ6Y'], 'also_viewed': ['B002J2KOXK']}",
       ..., "{'also_viewed': ['B00KSQ8ZNA', 'B00IPGI3A0', 'B00E68O4JU']}",
       "{'also_viewed': ['B0057JCYYE', 'B00LMXHR1Y', 'B00993T7YY', 'B006FRS9O6', 'B00993T6C2', 'B00CHV3LNS', 'B004NMYR96', 'B006HJQRB4', 'B007AU0FXA', 'B0053ZA1ME', 'B001RMP7M6', 'B00DLJ7LJA']}",


There are 51350 records with missing values in related column. We fill this column with dummy values.

In [14]:
data['related'] = data['related'].fillna("{'also_viewed': ['XYZ'], 'also_bought': ['XYZ'], 'bought_together': ['XYZ'], 'buy_after_viewing': ['XYZ']}")

Evaluate the literal/dict value in related column and copy just the asin and related columns into a new dataframe.

In [15]:
data['related'] = data['related'].apply(lambda x: ast.literal_eval(x))

In [16]:
result_related = data[['asin', 'related']].copy()
result_related.head()

asin                                            related
0  0205616461  {'also_viewed': ['XYZ'], 'also_bought': ['XYZ'...
1  0558925278  {'also_viewed': ['XYZ'], 'also_bought': ['XYZ'...
2  0733001998  {'also_viewed': ['XYZ'], 'also_bought': ['XYZ'...
3  0737104473  {'also_viewed': ['XYZ'], 'also_bought': ['XYZ'...
4  0762451459  {'also_viewed': ['XYZ'], 'also_bought': ['XYZ'...

Split the related column into separate columns for easier grouping. The 4 new columns will be also_bought, also_viewed, bought_together and buy_after_viewing. Drop the related column after the split.

In [17]:
df = result_related['related'].apply(pd.Series)
df2 = pd.concat([result_related, df], axis=1).drop('related', axis=1)

In [21]:
del beauty
del result_related
del df
del the_str

Fill the missing values in the new dataframe with dummy XYZ and then concatenate all the values in the 4 new columns as a string value.

In [18]:
df2 = df2.fillna("['XYZ']")

In [19]:
df2['related'] = df2["also_bought"].map(str)+df2["also_viewed"].map(str)+df2["bought_together"].map(str) + df2["buy_after_viewing"].map(str)

In [20]:
the_str = ','.join(map(str, df2['related']))
new_str = the_str.replace("['XYZ']",'')

For each row in the dataframe, check for the number of times it occurs in the concatenated string and assign that count to a new column "related_count".

In [22]:
for index, row in df2.iterrows():
    #print(result.related.str.count(row['asin']).sum())
    print(index,new_str.count(row['asin']))
    df2.loc[index,'related_count'] = new_str.count(row['asin'])

0 0
1 0
2 0
3 0
4 0
5 0
6 0
7 0
8 0
9 4
10 10
11 0
12 13
13 0
14 0
15 0
16 0
17 0
18 309
19 0
20 0
21 0
22 0
23 0
24 0
25 0
26 0
27 0
28 0
29 0
30 0
31 0
32 0
33 0
34 0
35 0
36 0
37 0
38 0
39 0
40 0
41 0
42 0
43 0
44 0
45 0
46 0
47 0
48 0
49 0
50 0
51 27
52 38
53 0
54 0
55 9
56 4
57 3
58 10
59 0
60 3
61 0
62 9
63 0
64 9
65 0
66 0
67 38
68 0
69 0
70 0
71 4
72 0
73 0
74 0
75 7
76 0
77 9
78 5
79 0
80 5
81 23
82 18
83 0
84 140
85 0
86 0
87 13
88 0
89 5
90 54
91 4
92 91
93 152
94 155
95 49
96 0
97 0
98 0
99 2
100 0
101 0
102 0
103 24
104 36
105 7
106 2
107 0
108 50
109 0
110 34
111 17
112 78
113 0
114 0
115 219
116 9
117 0
118 8
119 4
120 8
121 3
122 0
123 30
124 0
125 19
126 0
127 1
128 0
129 0
130 22
131 0
132 10
133 0
134 4
135 123
136 0
137 0
138 2
139 0
140 3
141 0
142 0
143 4
144 15
145 38
146 11
147 1
148 0
149 5
150 0
151 0
152 7
153 7
154 0
155 0
156 0
157 0
158 0
159 0
160 1
161 28
162 11
163 0
164 41
165 2
166 0
167 124
168 0
169 106
170 0
171 5
172 0
173 71
174 0
175 69
176 0
17

1281 22
1282 0
1283 0
1284 0
1285 0
1286 1
1287 0
1288 0
1289 2
1290 0
1291 0
1292 0
1293 0
1294 33
1295 0
1296 0
1297 0
1298 0
1299 3
1300 93
1301 0
1302 0
1303 15
1304 5
1305 0
1306 0
1307 0
1308 0
1309 0
1310 3
1311 2
1312 24
1313 0
1314 0
1315 0
1316 2
1317 0
1318 0
1319 0
1320 0
1321 0
1322 0
1323 0
1324 0
1325 6
1326 1
1327 0
1328 0
1329 0
1330 0
1331 21
1332 0
1333 11
1334 0
1335 39
1336 25
1337 13
1338 0
1339 0
1340 0
1341 0
1342 0
1343 0
1344 0
1345 0
1346 3
1347 0
1348 0
1349 0
1350 9
1351 0
1352 0
1353 0
1354 0
1355 0
1356 0
1357 0
1358 0
1359 0
1360 0
1361 0
1362 22
1363 0
1364 0
1365 228
1366 199
1367 121
1368 0
1369 23
1370 42
1371 0
1372 0
1373 0
1374 11
1375 7
1376 7
1377 43
1378 0
1379 0
1380 0
1381 0
1382 88
1383 8
1384 1
1385 0
1386 1
1387 0
1388 0
1389 0
1390 0
1391 0
1392 1
1393 1
1394 0
1395 0
1396 0
1397 56
1398 0
1399 5
1400 0
1401 0
1402 0
1403 0
1404 0
1405 0
1406 0
1407 0
1408 48
1409 0
1410 0
1411 0
1412 0
1413 0
1414 0
1415 0
1416 0
1417 0
1418 0
1419 6
142

2421 0
2422 0
2423 0
2424 115
2425 112
2426 0
2427 0
2428 0
2429 1
2430 0
2431 0
2432 0
2433 0
2434 0
2435 2
2436 0
2437 42
2438 1
2439 105
2440 0
2441 0
2442 27
2443 0
2444 0
2445 0
2446 0
2447 0
2448 0
2449 0
2450 0
2451 0
2452 0
2453 0
2454 0
2455 0
2456 0
2457 0
2458 0
2459 0
2460 0
2461 0
2462 329
2463 0
2464 0
2465 0
2466 0
2467 0
2468 0
2469 0
2470 19
2471 0
2472 2
2473 55
2474 0
2475 86
2476 0
2477 0
2478 0
2479 50
2480 37
2481 0
2482 2
2483 0
2484 0
2485 2
2486 57
2487 0
2488 0
2489 52
2490 37
2491 1
2492 0
2493 0
2494 0
2495 0
2496 2
2497 0
2498 4
2499 195
2500 0
2501 0
2502 0
2503 10
2504 0
2505 0
2506 62
2507 0
2508 0
2509 0
2510 8
2511 0
2512 0
2513 4
2514 40
2515 4
2516 38
2517 0
2518 0
2519 0
2520 2
2521 0
2522 1
2523 0
2524 0
2525 6
2526 0
2527 125
2528 29
2529 0
2530 0
2531 25
2532 0
2533 16
2534 0
2535 3
2536 0
2537 1
2538 151
2539 0
2540 0
2541 0
2542 0
2543 135
2544 0
2545 7
2546 0
2547 0
2548 0
2549 1
2550 17
2551 0
2552 70
2553 0
2554 9
2555 0
2556 0
2557 0
2558 0

3545 18
3546 5
3547 13
3548 9
3549 1
3550 30
3551 20
3552 0
3553 0
3554 0
3555 7
3556 1
3557 0
3558 0
3559 5
3560 3
3561 0
3562 10
3563 0
3564 6
3565 0
3566 0
3567 7
3568 26
3569 0
3570 0
3571 1
3572 0
3573 1
3574 1
3575 0
3576 22
3577 0
3578 0
3579 0
3580 11
3581 0
3582 0
3583 0
3584 5
3585 0
3586 47
3587 0
3588 1
3589 0
3590 0
3591 3
3592 3
3593 6
3594 0
3595 3
3596 0
3597 118
3598 0
3599 2
3600 0
3601 0
3602 0
3603 12
3604 0
3605 0
3606 0
3607 1
3608 4
3609 0
3610 0
3611 12
3612 0
3613 1
3614 0
3615 0
3616 0
3617 4
3618 1
3619 51
3620 0
3621 0
3622 2
3623 4
3624 0
3625 0
3626 0
3627 0
3628 0
3629 0
3630 8
3631 0
3632 0
3633 1
3634 1
3635 0
3636 1
3637 0
3638 17
3639 0
3640 1
3641 5
3642 6
3643 0
3644 0
3645 0
3646 0
3647 0
3648 5
3649 10
3650 4
3651 17
3652 0
3653 1
3654 15
3655 64
3656 0
3657 0
3658 0
3659 32
3660 25
3661 0
3662 0
3663 53
3664 0
3665 12
3666 35
3667 1
3668 57
3669 46
3670 4
3671 0
3672 181
3673 0
3674 0
3675 1
3676 0
3677 3
3678 0
3679 0
3680 0
3681 0
3682 5
3683 0

4673 3
4674 0
4675 0
4676 0
4677 0
4678 123
4679 0
4680 0
4681 0
4682 0
4683 0
4684 16
4685 0
4686 0
4687 0
4688 0
4689 0
4690 0
4691 0
4692 0
4693 0
4694 0
4695 43
4696 0
4697 0
4698 0
4699 0
4700 0
4701 0
4702 0
4703 0
4704 0
4705 0
4706 6
4707 0
4708 1
4709 0
4710 4
4711 29
4712 0
4713 5
4714 1
4715 0
4716 2
4717 48
4718 0
4719 0
4720 0
4721 122
4722 2
4723 0
4724 0
4725 0
4726 13
4727 0
4728 0
4729 0
4730 314
4731 18
4732 0
4733 23
4734 0
4735 0
4736 0
4737 32
4738 0
4739 3
4740 0
4741 0
4742 0
4743 9
4744 0
4745 0
4746 0
4747 0
4748 0
4749 5
4750 0
4751 21
4752 1
4753 0
4754 0
4755 1
4756 1
4757 1
4758 0
4759 0
4760 0
4761 15
4762 0
4763 0
4764 0
4765 0
4766 0
4767 7
4768 0
4769 20
4770 0
4771 0
4772 5
4773 0
4774 0
4775 0
4776 9
4777 0
4778 0
4779 0
4780 0
4781 0
4782 0
4783 0
4784 0
4785 10
4786 18
4787 0
4788 6
4789 0
4790 0
4791 0
4792 0
4793 0
4794 9
4795 10
4796 0
4797 15
4798 0
4799 0
4800 0
4801 0
4802 0
4803 0
4804 1
4805 0
4806 0
4807 0
4808 0
4809 0
4810 0
4811 0
4812 0

...

255662 152
255663 1
255664 0
255665 210
255666 4
255667 64
255668 1
255669 113
255670 0
255671 0
255672 0
255673 0
255674 0
255675 95
255676 0
255677 91
255678 22
255679 0
255680 0
255681 0
255682 0
255683 0
255684 0
255685 13
255686 12
255687 102
255688 2
255689 18
255690 0
255691 3
255692 10
255693 4
255694 0
255695 54
255696 0
255697 2
255698 0
255699 0
255700 0
255701 0
255702 56
255703 78
255704 4
255705 9
255706 4
255707 4
255708 17
255709 0
255710 0
255711 119
255712 30
255713 29
255714 0
255715 110
255716 0
255717 3
255718 17
255719 99
255720 40
255721 55
255722 0
255723 0
255724 0
255725 0
255726 32
255727 73
255728 0
255729 0
255730 0
255731 0
255732 0
255733 7
255734 0
255735 10
255736 0
255737 0
255738 10
255739 1
255740 0
255741 0
255742 0
255743 0
255744 7
255745 1
255746 0
255747 7
255748 0
255749 0
255750 1
255751 1
255752 0
255753 0
255754 0
255755 2
255756 3
255757 0
255758 0
255759 0
255760 0
255761 5
255762 2
255763 0
255764 1
255765 4
255766 2
255767 6
255768 24
25

256544 0
256545 10
256546 2
256547 0
256548 0
256549 0
256550 0
256551 1
256552 0
256553 3
256554 81
256555 0
256556 0
256557 2
256558 0
256559 9
256560 0
256561 1
256562 4
256563 2
256564 6
256565 24
256566 0
256567 0
256568 0
256569 0
256570 16
256571 5
256572 4
256573 37
256574 0
256575 18
256576 0
256577 30
256578 0
256579 0
256580 16
256581 2
256582 0
256583 6
256584 0
256585 1
256586 0
256587 6
256588 5
256589 1
256590 0
256591 9
256592 0
256593 3
256594 13
256595 22
256596 5
256597 3
256598 39
256599 0
256600 3
256601 5
256602 12
256603 2
256604 0
256605 1
256606 1
256607 1
256608 40
256609 0
256610 0
256611 3
256612 0
256613 107
256614 0
256615 124
256616 3
256617 0
256618 0
256619 0
256620 0
256621 38
256622 0
256623 2
256624 1
256625 136
256626 0
256627 0
256628 0
256629 0
256630 11
256631 36
256632 0
256633 0
256634 0
256635 0
256636 0
256637 0
256638 0
256639 0
256640 15
256641 3
256642 16
256643 0
256644 5
256645 22
256646 11
256647 0
256648 0
256649 0
256650 2
256651 38
2

257421 0
257422 11
257423 1
257424 1
257425 0
257426 7
257427 0
257428 0
257429 39
257430 0
257431 0
257432 13
257433 4
257434 32
257435 11
257436 5
257437 216
257438 5
257439 8
257440 112
257441 9
257442 0
257443 0
257444 16
257445 9
257446 5
257447 7
257448 36
257449 141
257450 11
257451 0
257452 248
257453 0
257454 131
257455 120
257456 0
257457 7
257458 0
257459 53
257460 20
257461 0
257462 10
257463 0
257464 0
257465 8
257466 4
257467 15
257468 14
257469 0
257470 3
257471 6
257472 30
257473 24
257474 13
257475 0
257476 117
257477 0
257478 0
257479 20
257480 0
257481 0
257482 3
257483 0
257484 494
257485 0
257486 0
257487 0
257488 0
257489 0
257490 0
257491 5
257492 0
257493 0
257494 0
257495 8
257496 0
257497 0
257498 81
257499 0
257500 58
257501 1
257502 45
257503 0
257504 3
257505 7
257506 8
257507 8
257508 4
257509 0
257510 0
257511 21
257512 12
257513 4
257514 0
257515 417
257516 21
257517 0
257518 0
257519 0
257520 0
257521 97
257522 0
257523 0
257524 0
257525 0
257526 1
2575

258296 18
258297 7
258298 0
258299 8
258300 0
258301 0
258302 8
258303 6
258304 0
258305 11
258306 10
258307 0
258308 9
258309 8
258310 9
258311 9
258312 5
258313 10
258314 3
258315 0
258316 5
258317 7
258318 0
258319 0
258320 80
258321 0
258322 3
258323 0
258324 0
258325 0
258326 1
258327 5
258328 15
258329 23
258330 0
258331 0
258332 16
258333 48
258334 38
258335 5
258336 167
258337 6
258338 7
258339 34
258340 252
258341 0
258342 0
258343 24
258344 9
258345 0
258346 0
258347 40
258348 0
258349 10
258350 14
258351 1
258352 6
258353 8
258354 0
258355 0
258356 0
258357 1
258358 4
258359 79
258360 0
258361 12
258362 33
258363 0
258364 2
258365 1
258366 65
258367 3
258368 1
258369 3
258370 11
258371 0
258372 0
258373 0
258374 26
258375 0
258376 44
258377 55
258378 37
258379 1
258380 46
258381 0
258382 15
258383 0
258384 69
258385 28
258386 732
258387 0
258388 2
258389 0
258390 1
258391 1
258392 13
258393 0
258394 61
258395 2
258396 3
258397 0
258398 0
258399 0
258400 19
258401 55
258402 3

259175 26
259176 2
259177 0
259178 0
259179 86
259180 0
259181 5
259182 1
259183 0
259184 0
259185 0
259186 0
259187 1
259188 0
259189 25
259190 17
259191 0
259192 35
259193 47
259194 1
259195 2
259196 1
259197 0
259198 0
259199 0
259200 1
259201 0
259202 0
259203 3


This cell took 20 hours to execute. So it will not be possible to run it again. The data will be captured into a .csv file for further use.

The columns 'related', 'also_viewed', 'also_bought', 'bought_together', 'buy_after_viewing' can be dropped from the temporary dataframe now.

In [26]:
df2.head()

asin  related_count
0  0205616461            0.0
1  0558925278            0.0
2  0733001998            0.0
3  0737104473            0.0
4  0762451459            0.0

In [25]:
columns = ['related', 'also_viewed', 'also_bought', 'bought_together', 'buy_after_viewing' ]
df2.drop(columns, inplace=True, axis=1)

Write the dataframe with index, asin and related_count columns into a csv file.

In [27]:
df2.to_csv('cleaned_related.csv')

Finally, write the cleaned meta dataframe also to a .csv file.

In [29]:
data.to_csv('cleaned_meta.csv')